In [1]:
import pandas as pd
import numpy as np
import altair as alt
import gpxpy
import haversine as hs

with open('../gpx/yilan-wulling.gpx', 'r') as gpx_file:
    gpx = gpxpy.parse(gpx_file)

route_info = []

for track in gpx.tracks:
    for segment in track.segments:
        for point in segment.points:
           route_info.append({
               'latitude': point.latitude,
               'longitude': point.longitude,
               'elevation': point.elevation,
               'time': point.time
           })

route_df = pd.DataFrame(route_info)

In [2]:
# loop it for all points
# create a haversine function to calculate distance

def haversine_distance(lat1, lon1, lat2, lon2) -> float:
    distance = hs.haversine(
            point1 = (lat1,lon1),
            point2 = (lat2,lon2),
            unit = hs.Unit.METERS
    )
    return np.round(distance, 2)
    
distances = [np.nan]

for i in range(len(route_df)):
    if i == 0:
        continue
    else:
        distances.append(haversine_distance(
            lat1=route_df.iloc[i - 1]['latitude'],
            lon1=route_df.iloc[i - 1]['longitude'],
            lat2=route_df.iloc[i]['latitude'],
            lon2=route_df.iloc[i]['longitude']
        ))
        
route_df['distance'] = distances

In [3]:
route_df = route_df.loc[::10]

In [4]:
route_df

latitude   longitude   elevation                      time  distance
0      24.674256  121.768730    8.000000 2022-04-15 19:08:13+00:00       NaN
10     24.674656  121.768904    6.400000 2022-04-15 19:08:23+00:00      3.75
20     24.674948  121.768957    6.600000 2022-04-15 19:08:33+00:00      3.91
30     24.675223  121.768815    6.400000 2022-04-15 19:08:43+00:00      3.91
40     24.675273  121.768430    6.200000 2022-04-15 19:08:53+00:00      3.63
...          ...         ...         ...                       ...       ...
45760  23.966299  120.974111  501.399994 2022-04-16 16:08:26+00:00      7.86
45770  23.965633  120.974085  499.200012 2022-04-16 16:08:36+00:00      5.75
45780  23.965166  120.974110  498.200012 2022-04-16 16:08:46+00:00      2.75
45790  23.965012  120.974123  498.399994 2022-04-16 16:08:56+00:00      0.74
45800  23.965011  120.974105  498.799988 2022-04-16 16:09:06+00:00      0.00

[4581 rows x 5 columns]

In [17]:
map = alt.Chart(df).mark_line().encode(
    x = alt.X('longitude', scale=alt.Scale(zero=False)),
    y = alt.Y('latitude', scale=alt.Scale(zero=False)),
    order = 'total_dist'
)

map

alt.Chart(...)

In [8]:
route_df['elevation_diff'] = route_df['elevation'].diff()

In [9]:
route_df['time_diff'] = [] + list(route_df['time'].diff().apply(lambda x: x/np.timedelta64(1, 's')))
# route_df['time_diff'] = route_df['time'].diff().apply(lambda x: x/np.timedelta64(1, 's')).fillna(0)

In [10]:
route_df['speed'] = route_df['distance']/route_df['time_diff'] * 18 / 5 * 10

In [11]:
route_df['total_dist'] = np.cumsum(route_df['distance'])

In [12]:
route_df['km'] = np.ceil((route_df['total_dist']+0.01)/1000)

In [13]:
route_df = route_df.fillna(0)
route_df['km'] = route_df['km'].astype('int')

In [14]:
grouped = route_df.groupby('km').agg({'time':['min','max'],'elevation':['first','last']})
grouped['net_elevation'] = grouped['elevation']['last'] - grouped['elevation']['first']
grouped['net_time'] = grouped['time']['max'] - grouped['time']['min']
# .apply(lambda x:'{0,.0f}:{1:02d}'.format(np.floor(x.total_seconds()/60)))
grouped.columns = grouped.columns.get_level_values(0)

route_df = route_df.join(grouped.loc[:, ['net_elevation','net_time']], how='left', on='km')

In [15]:
df = route_df[['latitude', 'longitude', 'elevation', 'time', 'distance',
       'elevation_diff', 'time_diff', 'speed', 'total_dist', 'km',
       'net_elevation']]

In [16]:
df['total_dist'] = df['total_dist']/100

<ipython-input-16-aedc79805319>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['total_dist'] = df['total_dist']/100


In [18]:
df

latitude   longitude   elevation                      time  distance  \
0      24.674256  121.768730    8.000000 2022-04-15 19:08:13+00:00      0.00   
10     24.674656  121.768904    6.400000 2022-04-15 19:08:23+00:00      3.75   
20     24.674948  121.768957    6.600000 2022-04-15 19:08:33+00:00      3.91   
30     24.675223  121.768815    6.400000 2022-04-15 19:08:43+00:00      3.91   
40     24.675273  121.768430    6.200000 2022-04-15 19:08:53+00:00      3.63   
...          ...         ...         ...                       ...       ...   
45760  23.966299  120.974111  501.399994 2022-04-16 16:08:26+00:00      7.86   
45770  23.965633  120.974085  499.200012 2022-04-16 16:08:36+00:00      5.75   
45780  23.965166  120.974110  498.200012 2022-04-16 16:08:46+00:00      2.75   
45790  23.965012  120.974123  498.399994 2022-04-16 16:08:56+00:00      0.74   
45800  23.965011  120.974105  498.799988 2022-04-16 16:09:06+00:00      0.00   

       elevation_diff  time_diff   speed  total_dist  km  net_elevation  
0            0.000000        0.0   0.000      0.0000   0       0.000000  
10          -1.600000       10.0  13.500      0.0375   1      52.600000  
20           0.200000       10.0  14.076      0.0766   1      52.600000  
30          -0.200000       10.0  14.076      0.1157   1      52.600000  
40          -0.200000       10.0  13.068      0.1520   1      52.600000  
...               ...        ...     ...         ...  ..            ...  
45760       -1.000000       10.0  28.296    200.9835  21     -14.600037  
45770       -2.199982       10.0  20.700    201.0410  21     -14.600037  
45780       -1.000000       10.0   9.900    201.0685  21     -14.600037  
45790        0.199982       10.0   2.664    201.0759  21     -14.600037  
45800        0.399994       10.0   0.000    201.0759  21     -14.600037  

[4581 rows x 11 columns]

In [19]:
elevation = alt.Chart(df).mark_area().encode(
    x = alt.X('time'),
    y = alt.Y('elevation')
)

elevation

alt.Chart(...)

In [20]:
line = alt.Chart(df.iloc[::50, :]).mark_line().encode(
    x = alt.X('total_dist'),
    y = alt.Y('elevation')
)
line

alt.Chart(...)

In [23]:
nearest = alt.selection(type='single', nearest=True, on='mouseover',
                        fields=['total_dist'], empty='none')

selectors = alt.Chart(df.iloc[::50, :]).mark_point().encode(
    x='total_dist',
    opacity=alt.value(0),
).add_selection(
    nearest
)

points = line.mark_point(color='red').encode(
    opacity=alt.condition(nearest, alt.value(1), alt.value(0))
)

rules = alt.Chart(df.iloc[::50, :]).mark_rule(color='gray').encode(
    x='total_dist',
).transform_filter(
    nearest
)

line + line.mark_area() +selectors + points + rules

alt.LayerChart(...)

In [43]:
map_point = map.mark_point(color='red').encode(
    opacity=alt.condition(nearest, alt.value(1), alt.value(0))
)

map + map_point | line + line.mark_area() + selectors + points + rules | speed + rules

alt.HConcatChart(...)

In [34]:
df['speedr'] = df['speed'].rolling(30).mean()

In [35]:
speed = alt.Chart(df.iloc[::50, :]).mark_line().encode(
    x = alt.X('total_dist'),
    y = alt.Y('speedr'),
    order='total_dist'
)
speed

alt.Chart(...)

In [79]:
a = line.mark_area(opacity=0.5) + selectors + points + rules
b = speed + rules

In [80]:
final = alt.layer(a,b).resolve_scale(
    y = 'independent'
)

final

alt.LayerChart(...)

In [56]:
import folium

In [84]:
route_map = folium.Map(location=[24.523087833076715, 121.44864320755003], zoom_start=8, tiles='Stamen Terrain',width=450,height=450)

# start = folium.Marker(location=[24.674256,121.768730],popup="Starting Point",tooltip=folium.Tooltip("Start",permanent=True))
# start.add_to(route_map)
# end = folium.Marker(location=[23.965011,120.974105],popup="End Point",tooltip=folium.Tooltip("End",permanent=True))
# end.add_to(route_map)

folium.PolyLine(df[['latitude','longitude']],weight=6).add_to(route_map)

display(route_map)

In [67]:
map + map_point | final

alt.HConcatChart(...)